#### 学习向量: 理解什么是向量，理解向量相似度（cosine similarity）
1. Vector embeddings:https://platform.openai.com/docs/guides/embeddings 
2. 使用https://jina.ai/  提供的 embedding v4
3. 组织3个句子，其中2个语义更接近，尝试比较他们3个向量的相似度

文档：https://python.langchain.com/docs/integrations/text_embedding/jina/

In [ ]:
import os
from dotenv import load_dotenv

load_dotenv()
base_url = os.getenv('JINA_API_BASE_URL')
api_key = os.getenv('JINA_API_KEY')

In [10]:
from langchain_community.embeddings import JinaEmbeddings
import numpy as np

def cosine_similarity(x,y):
    num = x.dot(y.T)
    denom = np.linalg.norm(x) * np.linalg.norm(y)
    return num / denom

embeddings = JinaEmbeddings(
    jina_api_key=api_key,
    model_name="jina-embeddings-v4",
)

In [11]:
sentences = [
    "我非常喜欢在周末去公园散步",
    "每到周末我都会去公园走一走",
    "今天的天气非常寒冷"
]

embeddings_list = embeddings.embed_documents(sentences)

for i in range(len(sentences)):
    print(f"句子{i+1}的向量: {embeddings_list[i]}")

embeddings_array = np.array(embeddings_list)

print("\n句子之间的相似度：")
for i in range(len(sentences)):
    for j in range(i+1, len(sentences)):
        similarity = cosine_similarity(embeddings_array[i], embeddings_array[j])
        print(f"句子{i+1}和句子{j+1}的相似度: {similarity:.4f}")

句子1的向量: [-0.01080322265625, -0.0284423828125, -0.007598876953125, -0.00433349609375, -0.0032196044921875, 0.012451171875, -0.01080322265625, -0.03662109375, 0.008544921875, 0.04345703125, 0.00885009765625, 0.0235595703125, 0.03466796875, -0.0020904541015625, 0.0238037109375, 0.0009918212890625, 0.0030517578125, 0.017822265625, 0.07421875, -0.011962890625, 0.0191650390625, 0.00147247314453125, 0.038818359375, 0.0133056640625, -0.01025390625, -0.04150390625, -0.004364013671875, 0.00653076171875, 0.00823974609375, -0.00017833709716796875, 0.0220947265625, -0.005615234375, -0.0184326171875, -0.014892578125, -0.0172119140625, -0.0556640625, 0.005401611328125, 0.009521484375, -0.021484375, 0.033203125, 0.044677734375, -0.005706787109375, -0.0091552734375, -0.0084228515625, -0.0106201171875, -0.01190185546875, -0.062255859375, 0.05224609375, 0.01611328125, -0.052734375, 0.008056640625, -0.004119873046875, -0.00128936767578125, 0.000431060791015625, -0.0052490234375, 0.030517578125, 0.02160644

#### 向量数据库：https://docs.weaviate.io/weaviate/quickstart/local 
1. 本地安装 weaviate：
2. 学习基本的向量存储，Semantic search

In [12]:
import weaviate

def create_collection(client: weaviate.WeaviateClient, collection_name: str):
    """
    创建集合
    :param client: Weaviate 客户端
    :param collection_name: 集合名称
    """
    collection_obj = {
        "class": collection_name,
        "description": "test collection",
        "vectorizer": "none",
        "vectorIndexType": "hnsw",
        "vectorIndexConfig": {
            "distance": "cosine", # https://docs.weaviate.io/weaviate/config-refs/distances
            "efConstruction": 200,
            "maxConnections": 64
        },
        "properties": [
            {
                "name": "text",
                "description": "The text content",
                "dataType": ["text"],
                "tokenization": "word",
                "indexFilterable": True,
                "indexSearchable": True
            }
        ]
    }
    try:
        client.collections.create_from_dict(collection_obj)
        print(f"创建集合 '{collection_name}' 成功.")
    except weaviate.exceptions.UnexpectedStatusCodeException as e:
        print(f"创建集合异常: {e}")


def save_documents(client: weaviate.WeaviateClient, collection_name: str, documents: list, embeddings: list):
    """
    向集合中插入数据
    :param client: Weaviate 客户端
    :param collection_name: 集合名称
    :param documents: 文档列表
    :param embeddings: 文档对应的向量列表
    """
    collection = client.collections.get(collection_name)
    for i in range(len(documents)):
        content = documents[i]
        vector = embeddings[i]
        properties = {
            "text": content
        }
        try:
            uuid = collection.data.insert(properties=properties, vector=vector)
            print(f"文档添加内容: {content[:30]}..., uuid: {uuid}")
        except Exception as e:
            print(f"添加文档异常: {e}")

def query_vector_collection(client: weaviate.WeaviateClient, collection_name: str, query: str, k: int) -> list:
    """
    从集合中查询数据
    :param client: Weaviate 客户端
    :param collection_name: 集合名称
    :param query: 查询的【向量】
    :param k: 返回的结果数量
    :return: 查询结果列表
    """
    
    collection = client.collections.get(collection_name)
    response = collection.query.near_vector(
        near_vector=query,
        limit=k
    )
    documents = [res.properties['text'] for res in response.objects]
    return documents


d:\yusys\202507\ai_learning\.venv\Lib\site-packages\google\protobuf\runtime_version.py:98: UserWarning: Protobuf gencode version 5.29.0 is exactly one major version older than the runtime version 6.31.1 at v1/aggregate.proto. Please update the gencode to avoid compatibility violations in the next runtime release.
  warnings.warn(
d:\yusys\202507\ai_learning\.venv\Lib\site-packages\google\protobuf\runtime_version.py:98: UserWarning: Protobuf gencode version 5.29.0 is exactly one major version older than the runtime version 6.31.1 at v1/base.proto. Please update the gencode to avoid compatibility violations in the next runtime release.
  warnings.warn(
d:\yusys\202507\ai_learning\.venv\Lib\site-packages\google\protobuf\runtime_version.py:98: UserWarning: Protobuf gencode version 5.29.0 is exactly one major version older than the runtime version 6.31.1 at v1/base_search.proto. Please update the gencode to avoid compatibility violations in the next runtime release.
  warnings.warn(
d:\yusy

In [13]:
sentences = [
    "张三是法外狂徒",
    "FAISS是一个用于高效相似性搜索和密集向量聚类的库。",
    "LangChain是一个用于开发由语言模型驱动的应用程序的框架。"
]

embeddings_list = embeddings.embed_documents(sentences)

In [16]:
client = weaviate.connect_to_local()

# create_collection(client, "test_collection")

# save_documents(client, "test_collection", sentences, embeddings_list)

In [17]:
text = "张三是谁？"
query_vector = embeddings.embed_query(text)
results = query_vector_collection(client, "test_collection", query_vector, k=1)
print(f"\n问题：{text}")
for i, result in enumerate(results):
    print(f"查询结果 {i+1}: {result}")


问题：张三是谁？
查询结果 1: 张三是法外狂徒


#### Loading：读取不同类型文件，对于 pdf、docx 、excel 文件学会如何读取（资料自行下载，越复杂越好），并分别使用以下框架对文件进行读取，并理解他们的不同
1. https://github.com/Unstructured-IO/unstructured 
2. https://github.com/docling-project/docling 
3. PDF: [GitHub - pymupdf/PyMuPDF: PyMuPDF is a high performance Python library for data extraction, analysis,conversion & manipulation of PDF (and other) documents.](https://github.com/pymupdf/PyMuPDF)


In [1]:
pdf_path = 'data/rag.pdf'
docx_path = 'data/光的衍射.docx'
xlsx_path = 'data/movie.xlsx'

In [10]:
from unstructured.partition.auto import partition
from unstructured.partition.docx import partition_docx

# Unstructured 读取

# 读取PDF文件
print("=== 使用 Unstructured 读取 PDF ===")
pdf_elements = partition(filename=pdf_path)
print(f"PDF文档共有 {len(pdf_elements)} 个元素")
for i, element in enumerate(pdf_elements[:3]):  # 只显示前3个元素
    print(f"元素 {i+1} - 类型: {type(element).__name__}")
    print(f"内容: {str(element)[:100]}...")
    print("元数据详情:")
    if hasattr(element, 'metadata') and element.metadata:
        for key, value in element.metadata.__dict__.items():
            if key not in ['text_as_html', 'languages', '_known_field_names', 'coordinates']:
                print(f"  {key}: {value}")
    else:
        print("  无元数据")
    print("-" * 50)

# 读取DOCX文件
print("\n=== 使用 Unstructured 读取 DOCX ===")
docx_elements = partition_docx(filename=docx_path)
print(f"DOCX文档共有 {len(docx_elements)} 个元素")
for i, element in enumerate(docx_elements[:3]):  # 只显示前3个元素
    print(f"元素 {i+1} - 类型: {type(element).__name__}")
    print(f"内容: {str(element)[:100]}...")
    print("元数据详情:")
    if hasattr(element, 'metadata') and element.metadata:
        for key, value in element.metadata.__dict__.items():
            if key not in ['text_as_html', 'languages', '_known_field_names']:
                print(f"  {key}: {value}")
    else:
        print("  无元数据")
    print("-" * 50)

# 读取XLSX文件
print("\n=== 使用 Unstructured 读取 XLSX ===")
xlsx_elements = partition(filename=xlsx_path)
print(f"XLSX文档共有 {len(xlsx_elements)} 个元素")
for i, element in enumerate(xlsx_elements[:2]):  # 只显示前2个元素
    print(f"元素 {i+1} - 类型: {type(element).__name__}")
    print(f"内容: {str(element)[:100]}...")
    print("元数据详情:")
    if hasattr(element, 'metadata') and element.metadata:
        for key, value in element.metadata.__dict__.items():
            if key not in ['text_as_html', 'languages', '_known_field_names']:
                print(f"  {key}: {value}")
    else:
        print("  无元数据")
    print("-" * 50)


Could get FontBBox from font descriptor because None cannot be parsed as 4 floats
Could get FontBBox from font descriptor because None cannot be parsed as 4 floats
Could get FontBBox from font descriptor because None cannot be parsed as 4 floats
Could get FontBBox from font descriptor because None cannot be parsed as 4 floats
Could get FontBBox from font descriptor because None cannot be parsed as 4 floats
Could get FontBBox from font descriptor because None cannot be parsed as 4 floats
Could get FontBBox from font descriptor because None cannot be parsed as 4 floats
Could get FontBBox from font descriptor because None cannot be parsed as 4 floats
Could get FontBBox from font descriptor because None cannot be parsed as 4 floats
Could get FontBBox from font descriptor because None cannot be parsed as 4 floats
Could get FontBBox from font descriptor because None cannot be parsed as 4 floats
Could get FontBBox from font descriptor because None cannot be parsed as 4 floats
Could get FontBB

=== 使用 Unstructured 读取 PDF ===


Could get FontBBox from font descriptor because None cannot be parsed as 4 floats
Could get FontBBox from font descriptor because None cannot be parsed as 4 floats
Could get FontBBox from font descriptor because None cannot be parsed as 4 floats
Could get FontBBox from font descriptor because None cannot be parsed as 4 floats
Could get FontBBox from font descriptor because None cannot be parsed as 4 floats
Could get FontBBox from font descriptor because None cannot be parsed as 4 floats
Could get FontBBox from font descriptor because None cannot be parsed as 4 floats
Could get FontBBox from font descriptor because None cannot be parsed as 4 floats
Could get FontBBox from font descriptor because None cannot be parsed as 4 floats
Could get FontBBox from font descriptor because None cannot be parsed as 4 floats
Could get FontBBox from font descriptor because None cannot be parsed as 4 floats
Could get FontBBox from font descriptor because None cannot be parsed as 4 floats
Could get FontBB

short text: "Printed using PDFCrowd". Defaulting to English.
short text: "HTML to PDF". Defaulting to English.
short text: "simayi315". Defaulting to English.
short text: "54hehezi". Defaulting to English.
short text: "Printed using PDFCrowd". Defaulting to English.
short text: "HTML to PDF". Defaulting to English.
short text: "Printed using PDFCrowd". Defaulting to English.
short text: "HTML to PDF". Defaulting to English.
short text: "Printed using PDFCrowd". Defaulting to English.
short text: "HTML to PDF". Defaulting to English.
short text: "5". Defaulting to English.
short text: "2". Defaulting to English.
short text: "4". Defaulting to English.
short text: "5". Defaulting to English.
short text: "6". Defaulting to English.
short text: "7". Defaulting to English.
short text: "8". Defaulting to English.
short text: "9". Defaulting to English.
short text: "10". Defaulting to English.
short text: "Printed using PDFCrowd". Defaulting to English.
short text: "HTML to PDF". Defaulting t

PDF文档共有 279 个元素
元素 1 - 类型: Header
内容: 网页...
元数据详情:
  file_directory: data
  filename: rag.pdf
  last_modified: 2025-07-30T15:29:52
  links: []
  page_number: 1
  filetype: application/pdf
--------------------------------------------------
元素 2 - 类型: Header
内容: 新闻...
元数据详情:
  file_directory: data
  filename: rag.pdf
  last_modified: 2025-07-30T15:29:52
  links: []
  page_number: 1
  filetype: application/pdf
--------------------------------------------------
元素 3 - 类型: Header
内容: 贴吧...
元数据详情:
  file_directory: data
  filename: rag.pdf
  last_modified: 2025-07-30T15:29:52
  links: []
  page_number: 1
  filetype: application/pdf
--------------------------------------------------

=== 使用 Unstructured 读取 DOCX ===
DOCX文档共有 48 个元素
元素 1 - 类型: Header
内容: 华南理工大学大学城校区物理实验报告...
元数据详情:
  category_depth: 0
  file_directory: data
  filename: 光的衍射.docx
  header_footer_type: primary
  filetype: application/vnd.openxmlformats-officedocument.wordprocessingml.document
-------------------------------------

In [14]:
# Docling 读取
from docling.document_converter import DocumentConverter, PdfFormatOption
from docling.datamodel.pipeline_options import EasyOcrOptions, PdfPipelineOptions
from docling.datamodel.base_models import InputFormat

artifacts_path = "../../../docling-models"
pipeline_options = PdfPipelineOptions(artifacts_path=artifacts_path)

# 初始化文档转换器
converter = DocumentConverter(
    format_options={
        InputFormat.PDF: PdfFormatOption(pipeline_options=pipeline_options)
    }
)

print("=== 使用 Docling 读取 PDF ===")
pdf_result_docling = converter.convert(pdf_path)
print(f"PDF文档标题: {pdf_result_docling.document.name}")
print(f"PDF文档页数: {len(pdf_result_docling.document.pages)}")
print("前200个字符的内容:")
print(pdf_result_docling.document.export_to_markdown()[:200])
print("-" * 50)

print("\n=== 使用 Docling 读取 DOCX ===")
docx_result_docling = converter.convert(docx_path)
print(f"DOCX文档标题: {docx_result_docling.document.name}")
print(f"DOCX文档页数: {len(docx_result_docling.document.pages)}")
print("前200个字符的内容:")
print(docx_result_docling.document.export_to_markdown()[:200])
print("-" * 50)

print("\n=== 使用 Docling 读取 XLSX ===")
xlsx_result_docling = converter.convert(xlsx_path)
print(f"XLSX文档标题: {xlsx_result_docling.document.name}")
print(f"XLSX文档页数: {len(xlsx_result_docling.document.pages)}")
print("前200个字符的内容:")
print(xlsx_result_docling.document.export_to_markdown()[:200])
print("-" * 50)

=== 使用 Docling 读取 PDF ===


d:\yusys\202507\ai_learning\.venv\Lib\site-packages\torch\utils\data\dataloader.py:665: UserWarning: 'pin_memory' argument is set as true but no accelerator is found, then device pinned memory won't be used.
  warnings.warn(warn_msg)
d:\yusys\202507\ai_learning\.venv\Lib\site-packages\torch\utils\data\dataloader.py:665: UserWarning: 'pin_memory' argument is set as true but no accelerator is found, then device pinned memory won't be used.
  warnings.warn(warn_msg)
d:\yusys\202507\ai_learning\.venv\Lib\site-packages\torch\utils\data\dataloader.py:665: UserWarning: 'pin_memory' argument is set as true but no accelerator is found, then device pinned memory won't be used.
  warnings.warn(warn_msg)


PDF文档标题: rag
PDF文档页数: 5
前200个字符的内容:
▪

▪

<!-- image -->

进⼊词条

检索增强生成

全站搜索

帮助

近期有不法分子冒充百度百科官方人员，以删除词条为由威胁并敲诈相关企业。在此严正声明：百度百科是免费编辑平台，绝不存在收费代编服务，请勿上当受骗！ 详情

&gt;&gt;

<!-- image -->

收藏

11

3

同义词 RAG（⼤模型内化吸收知识的过程）⼀般指检索增强⽣成

本词条由中国科学
--------------------------------------------------

=== 使用 Docling 读取 DOCX ===
DOCX文档标题: 光的衍射
DOCX文档页数: 0
前200个字符的内容:
**光的衍射**

（年级：  专业：计算机类  姓名：  学号：）

**引言：** 光的衍射现象是光的波动性的一种表现。光的衍射决定了光学仪器的分辨本领。在现代光学技术中，光的衍射在光谱分析、结构分析、成像等方面得到了越来越广泛的应用。因此，研究衍射现象及其规律，在理论和实践上都有重要意义。

**一、实验目的**

（1）观察单缝衍射现象。

（2）学习如何使用光电器件测量光强的分布。

（
--------------------------------------------------

=== 使用 Docling 读取 XLSX ===
XLSX文档标题: movie
XLSX文档页数: 27
前200个字符的内容:
|   编号 | 电影名称   | 导演                               | 主演                                    |   年份 | 国家             | 分类           |   评分人数 |
|--------|------------|------------------------------------
--------------------------------------------------
